In [1]:
# https://cran.r-project.org/web/views/TimeSeries.html
# https://www.datacamp.com/tracks/time-series-with-r
# https://www.datascience.com/blog/introduction-to-forecasting-with-arima-in-r-learn-data-science-tutorials
# https://www.otexts.org/fpp/8/7

In [2]:
# install.packages('robust')
# install.packages('TSPred')

library(TSPred)
library(hexbin)
library(robust)
library(imputeTS)
library(tseries)
library(forecast)
library(fUnitRoots)
library(portes)
library(nortest)
library(tsoutliers)
library(boot)

Loading required package: fit.models



Attaching package: ‘tseries’



The following object is masked from ‘package:imputeTS’:

    na.remove



Loading required package: timeDate


Loading required package: timeSeries


Loading required package: fBasics


Loading required package: parallel


In [3]:
# T <- read.xls("Dados das estacoes com 2018.xlsx", sheet = 1, header = TRUE, stringsAsFactors = FALSE)
T <- read.csv("Dados das estacoes com 2018.csv")

In [4]:
head(T)

Ano Mes AnoF T_INMET T_ICEA UR_INMET UR_ICEA 
 
 1961 1 15/01/1961 26.38193 NA 80.32258 NA 
 1961 2 15/02/1961 26.53500 NA 79.60714 NA 
 1961 3 15/03/1961 26.70000 NA 78.28226 NA 
 1961 4 15/04/1961 26.64600 NA 77.70000 NA 
 1961 5 15/05/1961 25.50000 NA 73.04839 NA 
 1961 6 15/06/1961 22.78000 NA 67.89167 NA

In [5]:
sapply(T, class) # Verificando os tipos

Ano 
 'integer' 
 Mes 
 'integer' 
 AnoF 
 'factor' 
 T_INMET 
 'numeric' 
 T_ICEA 
 'numeric' 
 UR_INMET 
 'numeric' 
 UR_ICEA 
 'numeric'

# Análise da Temperatura

In [6]:
options(repr.plot.width=16, repr.plot.height=8)

T_INMET <- ts(T$T_INMET,start=c(1961,1),f=12)

jpeg("g1.jpg", width = 1000, height = 700)
plot(T_INMET)
dev.off()

plot(T_INMET)

png: 2

In [7]:
T_ICEA <- ts(T$T_ICEA,start=c(1961,1),f=12)

jpeg("g2.jpg", width = 1000, height = 700)
plot(T_ICEA)
dev.off()

plot(T_ICEA)

png: 2

### Observe que as séries possuem falhas. Inicialmente as preencheremos com uma regressão robusta entre INMET e ICEA.

In [8]:
options(repr.plot.width=10, repr.plot.height=10)

mod1 = lmRob(T_INMET ~ T_ICEA, data = T)
summary(mod1)

bin <- hexbin(T_ICEA, T_INMET, xbins=30)

jpeg("g3.jpg", width = 1000, height = 700)
plot(bin)
dev.off()

plot(bin)


Call:
lmRob(formula = T_INMET ~ T_ICEA, data = T)

Residuals:
    Min      1Q  Median      3Q     Max 
-3.8137 -0.7333 -0.1029  0.6328  5.7032 

Coefficients:
            Estimate Std. Error t value Pr(>|t|)    
(Intercept)  4.39915    0.77383   5.685 2.24e-08 ***
T_ICEA       0.80588    0.02864  28.142  < 2e-16 ***
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

Residual standard error: 0.9937 on 495 degrees of freedom
Multiple R-Squared: 0.4702 

Test for Bias:
            statistic   p-value
M-estimate      9.596 8.246e-03
LS-estimate    45.666 1.213e-10
194 observations deleted due to missingness 

png: 2

In [9]:
aux <- T[is.na(T$T_INMET)&!is.na(T$T_ICEA),]
head(aux)

Ano Mes AnoF T_INMET T_ICEA UR_INMET UR_ICEA 
 
 349 1990 1 15/01/1990 NA 27.52 NA 75.2 
 350 1990 2 15/02/1990 NA 27.01 NA 78.4 
 351 1990 3 15/03/1990 NA 27.93 NA 74.8 
 352 1990 4 15/04/1990 NA 27.41 NA 74.0 
 353 1990 5 15/05/1990 NA 25.06 NA 75.6 
 354 1990 6 15/06/1990 NA 23.97 NA 77.7

In [10]:
aux <- predict(mod1, newdata=T[is.na(T$T_INMET)&!is.na(T$T_ICEA),]) # Estima INMET com base no ICEA

In [11]:
head(aux)

349 
 26.5770507637899 
 350 
 26.1660503977684 
 351 
 26.9074628227484 
 352 
 26.4884036260206 
 353 
 24.594578410039 
 354 
 23.7161658630518

In [12]:
# T[is.na(T$T_INMET)&!is.na(T$T_ICEA),] <- aux

In [13]:
T[is.na(T$T_INMET)&!is.na(T$T_ICEA),'T_INMET'] <- aux

In [14]:
T_INMET <- ts(T$T_INMET,start=c(1961,1),f=12)
plot(T_INMET)

In [15]:
# As falhas que sobraram foram preenchidas pelo estimador de Kalman.
T_INMET <- na.kalman(T_INMET, model = "auto.arima")

options(repr.plot.width=16, repr.plot.height=8)

jpeg("g4.jpg", width = 1000, height = 700)
plot(T_INMET)
dev.off()

plot(T_INMET)

png: 2

# Análise da Umidade Relativa

In [16]:
UR_INMET <- ts(T$UR_INMET,start=c(1961,1),f=12)
plot(UR_INMET)

In [17]:
UR_ICEA <- ts(T$UR_ICEA,start=c(1961,1),f=12)
plot(UR_ICEA)

Observe que as séries possuem falhas. Inicialmente as preencheremos com uma regressão entre INMET e ICEA.

In [18]:
mod2 = lmRob(UR_INMET ~ UR_ICEA, data = T)
summary(mod2)

bin <- hexbin(UR_INMET, UR_ICEA, xbins=30)
plot(bin)


Call:
lmRob(formula = UR_INMET ~ UR_ICEA, data = T)

Residuals:
     Min       1Q   Median       3Q      Max 
-14.8431  -2.7160  -0.1321   2.7989  16.2860 

Coefficients:
            Estimate Std. Error t value Pr(>|t|)    
(Intercept) 14.02245    1.56939   8.935   <2e-16 ***
UR_ICEA      0.86527    0.02302  37.593   <2e-16 ***
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

Residual standard error: 4.127 on 432 degrees of freedom
Multiple R-Squared: 0.5769 

Test for Bias:
            statistic   p-value
M-estimate      7.301 2.598e-02
LS-estimate    26.278 1.967e-06
257 observations deleted due to missingness 

In [19]:
aux <- T[is.na(T$UR_INMET)&!is.na(T$UR_ICEA),]
head(aux)

Ano Mes AnoF T_INMET T_ICEA UR_INMET UR_ICEA 
 
 217 1979 1 15/01/1979 26.40 27.56 NA 78.8 
 218 1979 2 15/02/1979 26.68 27.51 NA 77.8 
 219 1979 3 15/03/1979 26.36 27.63 NA 78.8 
 220 1979 4 15/04/1979 25.35 26.23 NA 77.7 
 221 1979 5 15/05/1979 24.63 26.33 NA 70.8 
 222 1979 6 15/06/1979 21.82 24.14 NA 65.4

In [20]:
aux <- predict(mod2, newdata=T[is.na(T$UR_INMET)&!is.na(T$UR_ICEA),]) # Estima INMET com base no ICEA

In [21]:
head(aux)

217 
 82.2057788962603 
 218 
 81.3405082703494 
 219 
 82.2057788962603 
 220 
 81.2539812077583 
 221 
 75.283613888973 
 222 
 70.611152509054

In [22]:
T[is.na(T$UR_INMET)&!is.na(T$UR_ICEA),'UR_INMET'] <- aux

In [23]:
UR_INMET <- ts(T$UR_INMET,start=c(1961,1),f=12)
plot(UR_INMET)

In [24]:
# As falhas que sobraram foram preenchidas pelo estimador de Kalman.
UR_INMET <- na.kalman(UR_INMET, model = "auto.arima")
plot(UR_INMET)

# Cálculo do índice térmico

In [25]:
install.packages('weathermetrics')

Installing package into ‘/home/user/R/x86_64-pc-linux-gnu-library/3.4’
(as ‘lib’ is unspecified)


In [26]:
library(weathermetrics)

In [27]:
it <- heat.index(t=T_INMET, rh=UR_INMET, temperature.metric="celsius", output.metric="celsius", round=2)
it <- ts(it,start=c(1961,1),f=12)

jpeg("g9.jpg", width = 1000, height = 700)
plot(it)
dev.off()

plot(it)

png: 2

In [28]:
# Decomposição da série temporal (aditiva, possivelmente baseada na transformáda rápida de Fourier, e apenas para fins de análise preliminar)

jpeg("g10.jpg", width = 1000, height = 700)
plot(decompose(it))
dev.off()

plot(decompose(it))

png: 2

# ARIMA

Etapas:
a) Verificar se existe a necessidade de uma transformação na série original, com objetivo de estabilizar a variância;
b) Tornar a série estacionária por meio de diferenças, de modo que o processo dZt seja reduzido a um ARMA(p,q)
c) Identificar o processo ARMA(p,q) resultante.
d) Verificação da estacionariedade e da invertibilidade.


FAC : correlação simples entre Zt e Zt – k em função da defasagem k.
FACP: correlação entre Zt e Zt – k em função da defasagem k, filtrado o efeito de todas as outras defasagens sobre Zt e Zt – k.

FACP -> AR

D -> I

FAC -> MA

1- Número de AR (auto-regressivo) termos (p): termos AR são apenas defasagens da variável dependente. Por exemplo, se o símbolo p representa 5, os preditores de x (t) irá ser X (t-1) … .x (T-5).
2-  Número de MA (média móvel) termos (q): termos MA estão defasados erros de previsão na equação de predição. Por exemplo, se q é 5, os preditores para x (t) será E (t-1) … .e (t-5) onde e (i) é a diferença entre a média móvel ao valor imediato e real.
3- Número de Diferenças (d): Estes são o número de diferenças não sazonal, ou seja, neste caso, tomamos a primeira diferença de ordem. Assim, ou nós podemos passar essa variável e colocar d = 0, ou passar a variável original e coloca -d = 1. Ambos irão gerar mesmos resultados.

Notação: arima(p, d, q), sendo p relacionado a autocorrelação parcial, d a diferença entre os valores, q associado a autocorrelação).

## Testes da estacionariedade da série

In [29]:
urkpssTest(it, type = c("tau"), lags = c("short"),use.lag = NULL, doplot = TRUE)


Title:
 KPSS Unit Root Test

Test Results:
  NA

Description:
 Thu Oct 18 18:23:32 2018 by user: 


In [30]:
adf.test(it, alternative="stationary")

Warning message in adf.test(it, alternative = "stationary"):
“p-value smaller than printed p-value”


	Augmented Dickey-Fuller Test

data:  it
Dickey-Fuller = -14.159, Lag order = 8, p-value = 0.01
alternative hypothesis: stationary


In [31]:
jpeg("g11.jpg", width = 1000, height = 700)
acf(it)
dev.off()
acf(it)

jpeg("g12.jpg", width = 1000, height = 700)
pacf(it)
dev.off()
pacf(it)

png: 2

png: 2

### Se rejeitarmos a hipótese da estacionariedade, desta forma, partimos de d=1.

In [32]:
ndiffs(it) # Valor de d para fazer a série estacionária.

1

In [33]:
# Calculando as correlações para uma diferença de ordem 1
jpeg("g12.jpg", width = 1000, height = 700)
acf(diff(it, differences=1))
dev.off()
acf(diff(it, differences=1))

jpeg("g13.jpg", width = 1000, height = 700)
pacf(diff(it, differences=1))
dev.off()
pacf(diff(it, differences=1))

png: 2

png: 2

Como o ACF cai depois do primeiro lag, podemos partir de p = 1-3.  Para o PACF o q poderia ser igual a 2, temos, então, um ARIMA(p, d, q) = ARIMA (1, 1, 2) com os mesmos parâmetros para sazonalidade.

## Ajustando os modelos

In [34]:
ajuste_0 <- Arima(it, c(1, 1, 2)) # Sem sazonalidade
ajuste_0

Series: it 
ARIMA(1,1,2) 

Coefficients:
          ar1     ma1     ma2
      -0.2744  0.3753  0.0765
s.e.   0.3108  0.3057  0.0477

sigma^2 estimated as 4.389:  log likelihood=-1487.86
AIC=2983.72   AICc=2983.78   BIC=3001.87

In [35]:
ajuste_1 <- Arima(it, c(1, 1, 2), seasonal=list(order = c(1, 1, 2), period = 12)) # Com sazonalidade
ajuste_1

Series: it 
ARIMA(1,1,2)(1,1,2)[12] 

Coefficients:
         ar1      ma1     ma2     sar1     sma1     sma2
      0.5930  -1.3374  0.3538  -0.9781  -0.0084  -0.9405
s.e.  0.1312   0.1503  0.1430   0.0489   0.0696   0.0716

sigma^2 estimated as 1.513:  log likelihood=-1119.62
AIC=2253.23   AICc=2253.4   BIC=2284.87

### Utilizando via auto.arima

In [36]:
# Automatizando
ajuste_auto <- auto.arima(it, stepwise=FALSE, approximation=FALSE, trace=TRUE)
ajuste_auto


 ARIMA(0,0,0)(0,1,0)[12]                    : 2686.114
 ARIMA(0,0,0)(0,1,0)[12] with drift         : 2688.049
 ARIMA(0,0,0)(0,1,1)[12]                    : 2324.46
 ARIMA(0,0,0)(0,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(0,1,2)[12]                    : 2326.375
 ARIMA(0,0,0)(0,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,0)[12]                    : 2477.808
 ARIMA(0,0,0)(1,1,0)[12] with drift         : 2479.523
 ARIMA(0,0,0)(1,1,1)[12]                    : 2326.363
 ARIMA(0,0,0)(1,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,2)[12]                    : Inf
 ARIMA(0,0,0)(1,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,0)[12]                    : 2394.978
 ARIMA(0,0,0)(2,1,0)[12] with drift         : 2396.522
 ARIMA(0,0,0)(2,1,1)[12]                    : 2326.994
 ARIMA(0,0,0)(2,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,2)[12]                    : 2330.21
 ARIMA(0,0,0)(2,1,2)[12] with drift         : Inf
 ARIMA(0,0,1)(0,1,0)[12]                    : 

Series: it 
ARIMA(1,0,0)(0,1,1)[12] 

Coefficients:
         ar1     sma1
      0.2988  -0.8859
s.e.  0.0375   0.0245

sigma^2 estimated as 1.592:  log likelihood=-1129.63
AIC=2265.25   AICc=2265.29   BIC=2278.82

### No caso, obteve um AIC maior, mas com SE menores. Pelo princípio da parcimônia, e sabendo que existe sazonalidade, utilizaremos, de início, o modelo (0,0,2)(0,1,1)12.

In [37]:
acf(ajuste_auto$residuals)
pacf(ajuste_auto$residuals)

In [38]:
jpeg("g14.jpg", width = 1000, height = 700)
qqnorm(ajuste_auto$residuals)
qqline(ajuste_auto$residuals)
dev.off()

qqnorm(ajuste_auto$residuals)
qqline(ajuste_auto$residuals)

lillie.test(ajuste_auto$residuals)

png: 2


	Lilliefors (Kolmogorov-Smirnov) normality test

data:  ajuste_auto$residuals
D = 0.04776, p-value = 0.0007485


### Não adere a Normal, mas também não apresenta comportamento anômalo. É o caso de tentar uma transformação de Box-Cox.

In [39]:
l <- BoxCox.lambda(it)
l

-0.75570192309047

In [40]:
ajuste_auto_bc <- auto.arima(it, stepwise=FALSE, approximation=FALSE, trace=TRUE, lambda=l)
ajuste_auto_bc


 ARIMA(0,0,0)(0,1,0)[12]                    : -5184.219
 ARIMA(0,0,0)(0,1,0)[12] with drift         : -5182.264
 ARIMA(0,0,0)(0,1,1)[12]                    : -5533.35
 ARIMA(0,0,0)(0,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(0,1,2)[12]                    : -5531.396
 ARIMA(0,0,0)(0,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,0)[12]                    : -5382.485
 ARIMA(0,0,0)(1,1,0)[12] with drift         : -5380.732
 ARIMA(0,0,0)(1,1,1)[12]                    : -5531.404
 ARIMA(0,0,0)(1,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,2)[12]                    : Inf
 ARIMA(0,0,0)(1,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,0)[12]                    : -5456.414
 ARIMA(0,0,0)(2,1,0)[12] with drift         : -5454.814
 ARIMA(0,0,0)(2,1,1)[12]                    : -5531.065
 ARIMA(0,0,0)(2,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,2)[12]                    : Inf
 ARIMA(0,0,0)(2,1,2)[12] with drift         : Inf
 ARIMA(0,0,1)(0,1,0)[12]                

Series: it 
ARIMA(0,0,3)(0,1,1)[12] 
Box Cox transformation: lambda= -0.7557019 

Coefficients:
         ma1     ma2     ma3     sma1
      0.2236  0.1118  0.1139  -0.8862
s.e.  0.0388  0.0381  0.0353   0.0249

sigma^2 estimated as 1.526e-05:  log likelihood=2794.9
AIC=-5579.79   AICc=-5579.7   BIC=-5557.19

In [41]:
qqnorm(ajuste_auto_bc$residuals)
qqline(ajuste_auto_bc$residuals)
lillie.test(ajuste_auto_bc$residuals)
hist(ajuste_auto_bc$residuals)


	Lilliefors (Kolmogorov-Smirnov) normality test

data:  ajuste_auto_bc$residuals
D = 0.048052, p-value = 0.0006699


### Melhorou as estatísticas, mas não a questão da aderência a Normal. Tem outliers...

In [42]:
# A função não possui o parâmetro lambda
# outliers <- tso(BoxCox(it,l),tsmethod = "auto.arima", args.tsmethod = list(lambda=l), types = c("AO","LS","TC"))

In [43]:
outliers <- tso(BoxCox(it,l),tsmethod = "arima", args.tsmethod = list(order=c(0, 0, 3), seasonal=list(order=c(0, 1, 1), period=12)), types = c("AO","LS","TC"), maxit.iloop=50)

Warning message in locate.outliers.oloop(y = y, fit = fit, types = types, cval = cval, :
“stopped when 'maxit.oloop = 4' was reached”

In [44]:
outliers


Call:
structure(list(method = NULL), .Names = "method")

Coefficients:
         ma1     ma2     ma3     sma1    AO507
      0.2195  0.1154  0.1241  -0.8833  -0.0170
s.e.  0.0388  0.0378  0.0355   0.0252   0.0036

sigma^2 estimated as 1.468e-05:  log likelihood = 2805.82,  aic = -5599.64

Outliers:
  type ind    time  coefhat  tstat
1   AO 507 2003:03 -0.01704 -4.709

In [45]:
it[outliers$outliers$ind] <- NA

In [46]:
# Substituindo os outliers por estimativas...
it <- na.kalman(it, model = "auto.arima")

In [47]:
l <- BoxCox.lambda(it)
l

-0.706569225958772

In [48]:
outliers2 <- tso(BoxCox(it,l),tsmethod = "arima", args.tsmethod = list(order=c(1, 0, 2), seasonal=list(order=c(0, 1, 1), period=12)), types = c("AO","LS","TC"), maxit.iloop=50)
outliers2


Call:
structure(list(method = NULL), .Names = "method")

Coefficients:
         ar1      ma1      ma2     sma1     TC88
      0.9910  -0.7919  -0.1484  -0.9594  -0.0157
s.e.  0.0118   0.0388   0.0396   0.0317   0.0036

sigma^2 estimated as 1.922e-05:  log likelihood = 2709.07,  aic = -5406.15

Outliers:
  type ind    time  coefhat  tstat
1   TC  88 1968:04 -0.01565 -4.379

In [49]:
it[outliers2$outliers$ind] <- NA
it <- na.kalman(it, model = "auto.arima")
l <- BoxCox.lambda(it)
l

-0.83974114653526

In [50]:
outliers3 <- tso(BoxCox(it,l),tsmethod = "arima", args.tsmethod = list(order=c(1, 0, 2), seasonal=list(order=c(0, 1, 1), period=12)), types = c("AO","LS","TC"), maxit.iloop=50)
outliers3


Call:
structure(list(method = NULL), .Names = "method")

Coefficients:
         ar1      ma1      ma2     sma1     TC89
      0.9907  -0.7903  -0.1505  -0.9571  -0.0093
s.e.  0.0119   0.0388   0.0395   0.0306   0.0023

sigma^2 estimated as 8.025e-06:  log likelihood = 3005.94,  aic = -5999.88

Outliers:
  type ind    time  coefhat  tstat
1   TC  89 1968:05 -0.00934 -4.052

### Reajustando

In [51]:
# Reajustando
ajuste_auto_bc_outliers <- auto.arima(it, stepwise=FALSE, approximation=FALSE, trace=TRUE, lambda=l)
ajuste_auto_bc_outliers


 ARIMA(0,0,0)(0,1,0)[12]                    : -5595.614
 ARIMA(0,0,0)(0,1,0)[12] with drift         : -5593.661
 ARIMA(0,0,0)(0,1,1)[12]                    : -5935.103
 ARIMA(0,0,0)(0,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(0,1,2)[12]                    : -5933.397
 ARIMA(0,0,0)(0,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,0)[12]                    : -5784.9
 ARIMA(0,0,0)(1,1,0)[12] with drift         : -5783.151
 ARIMA(0,0,0)(1,1,1)[12]                    : -5933.43
 ARIMA(0,0,0)(1,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(1,1,2)[12]                    : -5931.091
 ARIMA(0,0,0)(1,1,2)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,0)[12]                    : -5857.596
 ARIMA(0,0,0)(2,1,0)[12] with drift         : -5856.001
 ARIMA(0,0,0)(2,1,1)[12]                    : -5932.721
 ARIMA(0,0,0)(2,1,1)[12] with drift         : Inf
 ARIMA(0,0,0)(2,1,2)[12]                    : Inf
 ARIMA(0,0,0)(2,1,2)[12] with drift         : Inf
 ARIMA(0,0,1)(0,1,0)[12]            

Series: it 
ARIMA(0,0,3)(0,1,1)[12] 
Box Cox transformation: lambda= -0.8397411 

Coefficients:
         ma1     ma2     ma3     sma1
      0.2070  0.1108  0.1212  -0.8823
s.e.  0.0387  0.0377  0.0356   0.0253

sigma^2 estimated as 8.5e-06:  log likelihood=2994.15
AIC=-5978.3   AICc=-5978.21   BIC=-5955.7

In [52]:
qqnorm(ajuste_auto_bc_outliers$residuals)
qqline(ajuste_auto_bc_outliers$residuals)
lillie.test(ajuste_auto_bc_outliers$residuals)
hist(ajuste_auto_bc_outliers$residuals)


	Lilliefors (Kolmogorov-Smirnov) normality test

data:  ajuste_auto_bc_outliers$residuals
D = 0.045034, p-value = 0.002032


# Testando o modelo

In [53]:
LjungBox(ajuste_auto_bc_outliers, lag=c(5, 10, 20, 25, 39, 35, 40, 45, 50), season=12) # Testa se existe autocorrelação entre os dados considerando a sazonalidade

lags statistic df p-value 
 
 5 1.062512 1 0.3026430 
 10 3.328105 6 0.7666811 
 20 12.336436 16 0.7205137 
 25 15.104615 21 0.8176662 
 39 22.618804 35 0.9473957 
 35 20.702034 31 0.9195489 
 40 23.485258 36 0.9463749 
 45 24.757322 41 0.9788522 
 50 27.181846 46 0.9877001

### Previsões para os próximos 3 meses

In [54]:
previsoes_auto_bc_outliers <- forecast(ajuste_auto_bc_outliers, h=3)
previsoes_auto_bc_outliers
accuracy(previsoes_auto_bc_outliers)

         Point Forecast    Lo 80    Hi 80    Lo 95    Hi 95
Aug 2018       26.33039 24.87485 27.95070 24.16290 28.88467
Sep 2018       28.98351 27.21961 30.96980 26.36381 32.12565
Oct 2018       30.73892 28.76825 32.97308 27.81667 34.28051

ME RMSE MAE MPE MAPE MASE ACF1 
 
 Training set 0.1303623 1.229289 0.9624951 0.2885044 3.526468 0.7180662 0.04779255

In [55]:
mod2 = lmRob(ajuste_auto_bc_outliers$x ~ ajuste_auto_bc_outliers$fitted, data = T)
summary(mod2)

options(repr.plot.width=8, repr.plot.height=8)
bin <- hexbin(ajuste_auto_bc_outliers$fitted, ajuste_auto_bc_outliers$x, xbins=30)

jpeg("g15.jpg", width = 1000, height = 700)
plot(bin)
dev.off()
plot(bin)

options(repr.plot.width=16, repr.plot.height=8)
jpeg("g16.jpg", width = 1000, height = 700)
ts.plot(ajuste_auto_bc_outliers$fitted,ajuste_auto_bc_outliers$x, lty=c(2,1), gpars = list(col = c("blue", "black")))
dev.off()
ts.plot(ajuste_auto_bc_outliers$fitted,ajuste_auto_bc_outliers$x, lty=c(2,1), gpars = list(col = c("blue", "black")))


Call:
lmRob(formula = ajuste_auto_bc_outliers$x ~ ajuste_auto_bc_outliers$fitted, 
    data = T)

Residuals:
      Min        1Q    Median        3Q       Max 
-3.915993 -0.759128  0.005429  0.725391  4.303154 

Coefficients:
                               Estimate Std. Error t value Pr(>|t|)    
(Intercept)                     0.59538    0.57686   1.032    0.302    
ajuste_auto_bc_outliers$fitted  0.98361    0.02091  47.032   <2e-16 ***
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

Residual standard error: 1.133 on 689 degrees of freedom
Multiple R-Squared: 0.5979 

Test for Bias:
            statistic   p-value
M-estimate     0.1828 9.127e-01
LS-estimate   39.6429 2.464e-09

png: 2

png: 2

In [56]:
jpeg("g17.jpg", width = 1000, height = 700)
plotarimapred(it, ajuste_auto_bc_outliers, xlim=c(2010, 2019))
dev.off()
plotarimapred(it, ajuste_auto_bc_outliers, xlim=c(2010, 2019))

png: 2

## Bootstrap

In [57]:
AIC_Boot <- function(ts) {
    aux <- Arima(ts, lambda=l, order=c(1, 0, 0), seasonal=list(order=c(0, 1, 1), period=12))
    return(aux$aic)
}

In [58]:
aux <- Arima(it, lambda=l, order=c(1, 0, 0), seasonal=list(order=c(0, 1, 1), period=12))

In [59]:
AIC_Boot(it)

-5971.77551730091

In [60]:
# Bootstrap estacionário com bloco de 20
boot_ajuste_auto_bc_outliers <- tsboot(it, AIC_Boot, R = 1000, l = 20, sim = "geom")

In [61]:
boot_ajuste_auto_bc_outliers


STATIONARY BOOTSTRAP FOR TIME SERIES

Average Block Length of 20 

Call:
tsboot(tseries = it, statistic = AIC_Boot, R = 1000, l = 20, 
    sim = "geom")


Bootstrap Statistics :
     original   bias    std. error
t1* -5971.776 673.5559    48.29323

In [62]:
boot.ci(boot_ajuste_auto_bc_outliers)

Warning message in boot.ci(boot_ajuste_auto_bc_outliers):
“bootstrap variances needed for studentized intervals”

Warning message in boot.ci(boot_ajuste_auto_bc_outliers):
“BCa intervals not defined for time series bootstraps”

BOOTSTRAP CONFIDENCE INTERVAL CALCULATIONS
Based on 1000 bootstrap replicates

CALL : 
boot.ci(boot.out = boot_ajuste_auto_bc_outliers)

Intervals : 
Level      Normal              Basic              Percentile     
95%   (-6740, -6551 )   (-6731, -6548 )   (-5395, -5213 )  
Calculations and Intervals on Original Scale